# Podatkovna znanost v oblaku: Način "Azure ML SDK"

## Uvod

V tem zvezku se bomo naučili, kako uporabljati Azure ML SDK za treniranje, uvajanje in uporabo modela prek Azure ML.

Predpogoji:
1. Ustvarili ste delovni prostor Azure ML.
2. Naložili ste [Heart Failure dataset](https://www.kaggle.com/andrewmvd/heart-failure-clinical-data) v Azure ML.
3. Naložili ste ta zvezek v Azure ML Studio.

Naslednji koraki so:

1. Ustvarite eksperiment v obstoječem delovnem prostoru.
2. Ustvarite računalniški grozd.
3. Naložite podatkovni niz.
4. Konfigurirajte AutoML z uporabo AutoMLConfig.
5. Zaženite AutoML eksperiment.
6. Raziščite rezultate in pridobite najboljši model.
7. Registrirajte najboljši model.
8. Uvedite najboljši model.
9. Uporabite končno točko.

## Uvozi, specifični za Azure Machine Learning SDK


In [ ]:
from azureml.core import Workspace, Experiment
from azureml.core.compute import AmlCompute
from azureml.train.automl import AutoMLConfig
from azureml.widgets import RunDetails
from azureml.core.model import InferenceConfig, Model
from azureml.core.webservice import AciWebservice

## Inicializacija delovnega prostora
Inicializirajte objekt delovnega prostora iz shranjene konfiguracije. Prepričajte se, da je konfiguracijska datoteka prisotna na poti .\config.json


In [ ]:
ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep = '\n')

## Ustvarite eksperiment Azure ML

Ustvarimo eksperiment z imenom 'aml-experiment' v delovnem prostoru, ki smo ga pravkar inicializirali.


In [ ]:
experiment_name = 'aml-experiment'
experiment = Experiment(ws, experiment_name)
experiment

## Ustvarite računski grozd
Za zagon AutoML boste morali ustvariti [računski cilj](https://docs.microsoft.com/azure/machine-learning/concept-azure-machine-learning-architecture#compute-target).


In [ ]:
aml_name = "heart-f-cluster"
try:
    aml_compute = AmlCompute(ws, aml_name)
    print('Found existing AML compute context.')
except:
    print('Creating new AML compute context.')
    aml_config = AmlCompute.provisioning_configuration(vm_size = "Standard_D2_v2", min_nodes=1, max_nodes=3)
    aml_compute = AmlCompute.create(ws, name = aml_name, provisioning_configuration = aml_config)
    aml_compute.wait_for_completion(show_output = True)

cts = ws.compute_targets
compute_target = cts[aml_name]

## Podatki
Prepričajte se, da ste naložili nabor podatkov v Azure ML in da je ključ enakega imena kot nabor podatkov.


In [ ]:
key = 'heart-failure-records'
dataset = ws.datasets[key]
df = dataset.to_pandas_dataframe()
df.describe()

## Konfiguracija AutoML


In [ ]:
automl_settings = {
    "experiment_timeout_minutes": 20,
    "max_concurrent_iterations": 3,
    "primary_metric" : 'AUC_weighted'
}

automl_config = AutoMLConfig(compute_target=compute_target,
                             task = "classification",
                             training_data=dataset,
                             label_column_name="DEATH_EVENT",
                             enable_early_stopping= True,
                             featurization= 'auto',
                             debug_log = "automl_errors.log",
                             **automl_settings
                            )

## Zagon AutoML


In [ ]:
remote_run = experiment.submit(automl_config)

In [ ]:
RunDetails(remote_run).show()

In [ ]:
best_run, fitted_model = remote_run.get_output()

In [ ]:
best_run.get_properties()

In [ ]:
model_name = best_run.properties['model_name']
script_file_name = 'inference/score.py'
best_run.download_file('outputs/scoring_file_v_1_0_0.py', 'inference/score.py')
description = "aml heart failure project sdk"
model = best_run.register_model(model_name = model_name,
                                description = description,
                                tags = None)

## Namestitev najboljšega modela

Za namestitev najboljšega modela zaženite naslednjo kodo. Stanje namestitve lahko preverite v portalu Azure ML. Ta korak lahko traja nekaj minut.


In [ ]:
inference_config = InferenceConfig(entry_script=script_file_name, environment=best_run.get_environment())

aciconfig = AciWebservice.deploy_configuration(cpu_cores = 1,
                                               memory_gb = 1,
                                               tags = {'type': "automl-heart-failure-prediction"},
                                               description = 'Sample service for AutoML Heart Failure Prediction')

aci_service_name = 'automl-hf-sdk'
aci_service = Model.deploy(ws, aci_service_name, [model], inference_config, aciconfig)
aci_service.wait_for_deployment(True)
print(aci_service.state)

## Uporaba končne točke
V spodnji vzorec vnosa lahko dodate svoje vnose.


In [ ]:
data = {
    "data":
    [
        {
            'age': "60",
            'anaemia': "false",
            'creatinine_phosphokinase': "500",
            'diabetes': "false",
            'ejection_fraction': "38",
            'high_blood_pressure': "false",
            'platelets': "260000",
            'serum_creatinine': "1.40",
            'serum_sodium': "137",
            'sex': "false",
            'smoking': "false",
            'time': "130",
        },
    ],
}

test_sample = str.encode(json.dumps(data))

In [ ]:
response = aci_service.run(input_data=test_sample)
response


---

**Omejitev odgovornosti**:  
Ta dokument je bil preveden z uporabo storitve za strojno prevajanje [Co-op Translator](https://github.com/Azure/co-op-translator). Čeprav si prizadevamo za natančnost, vas prosimo, da upoštevate, da lahko avtomatizirani prevodi vsebujejo napake ali netočnosti. Izvirni dokument v njegovem izvirnem jeziku je treba obravnavati kot avtoritativni vir. Za ključne informacije priporočamo strokovno človeško prevajanje. Ne prevzemamo odgovornosti za morebitna nesporazumevanja ali napačne razlage, ki izhajajo iz uporabe tega prevoda.
